## Using WMTS Protocol

In this example the geojson library is used to help find the bounding box of a scene. Be sure to install this library.

> pip install geojson

The math library is used to calculate the tile values for the WMTS request.

In [ ]:
import geojson
import json
import math
import requests

SEARCH_API_ENDPOINT = 'https://search.foundation.api.oneatlas.airbus.com/api/v2/opensearch'

access_token = input("Enter your access token")
scene_id = input("Enter the scene source identifier")
zoom_level = int(input("Enter a zoom level (-1 to 17)"))
download_path = input("Path to download to")

headers = {
    "Authorization": f"Bearer {access_token}"
}
body = {
    "sourceIdentifier": scene_id
}
response = requests.post(f"{SEARCH_API_ENDPOINT}", json=body, headers=headers)
response.raise_for_status()

body = response.json()
wmts_link = body['features'][0]['_links']['wms']['href']

The geojson library is used to load the geometry so it is easier to get to the coordinate pairs. Once available, the bounding box can be figured out from the coordinate list.

In [ ]:
geometry = geojson.base.GeoJSON.to_instance(body['features'][0]['geometry'])
min_x = min([x for x,y in list(geojson.utils.coords(geometry))])
max_x = max([x for x,y in list(geojson.utils.coords(geometry))])
min_y = min([y for x,y in list(geojson.utils.coords(geometry))])
max_y = max([y for x,y in list(geojson.utils.coords(geometry))])
bbox = f"{min_y},{min_x},{max_y},{max_x}"
print(f"Bounding box is {bbox}")

Compute the upper left and bottom right corner tile matrix values for the desired zoom level.


In [ ]:
DEGREES_2_RADIANS = math.pi / 180

matrix_width = math.pow(2, zoom_level) * 2
matrix_height = math.pow(2, zoom_level)

tile_x_min = math.floor(matrix_width * ((min_x * DEGREES_2_RADIANS + math.pi) / (2 * math.pi)))
tile_y_min = math.floor(matrix_height * (1 - (min_y * DEGREES_2_RADIANS + math.pi / 2) / math.pi))
tile_x_max = math.floor(matrix_width * ((max_x * DEGREES_2_RADIANS + math.pi) / (2 * math.pi)))
tile_y_max = math.floor(matrix_height * (1 - (max_y * DEGREES_2_RADIANS + math.pi / 2) / math.pi))

print(f"Tile Upper left corner: {tile_x_min},{tile_y_max}, Bottom right corner: {tile_x_max},{tile_y_min}")

Make a request for the upper left corner tile.

In [ ]:
url = f"{wmts_link}/tiles/1.0.0/default/rgb/EPSG4326/{zoom_level}/{tile_x_min}/{tile_y_min}.png"
print(f"Upper left corner URL : {url}")
with requests.get(url, headers=headers, stream=True) as r:
        r.raise_for_status()
        with open(download_path, 'wb') as f:
            for chunk in r.iter_content(chunk_size=8192): 
                f.write(chunk)
      
print(f"Downloaded to {download_path}")